### This script should load all models and return the set of modells having no errors
- Modelle in dict format {modelName: modelPath}
- Load and validate models (without error => try initial FBA)

In [45]:
# import + config
import cobra
import yaml # config file parsing
import sys # append path
import pandas as pd
from cobra.flux_analysis.parsimonious import pfba 

sys.path.append('../scripts/')
import helperFunction as hf

config = hf.load_config()

_verbose = config['verbose'] == 'True'
_verbose = True

In [37]:
# compare reports
def equal_reports(report_one, report_two):
    '''Returns True if the two reports are equal'''
    for key, value in report_one.items():
        if value != report_two[key]:
            return False
    return True
    
def show_differences(report_one, report_two):
    '''Returns a list of keys the two reports differ in'''
    different_keys = []
    for key, value in report_one.items():
        if value != report_two[key]:
            different_keys.append(key)
    return different_keys

# models dictionary
models = {
    'yli647_corr': config['models']['yli647_corr'], 
    'yli647_uncorr': config['models']['yli647_uncorr'], 
    'iYL619_PCP': config['models']['iYL619_PCP'], 
    'iYali4_corr': config['models']['yli4_corr'], 
    'iYali4_uncorr': config['models']['yli4_uncorr'], 
    'iYli_2.0_corr': config['models']['yli2.0_corr'], 
    'iMK735_corr': config['models']['yliMK735_corr'], 
    'iMK735_uncorr': config['models']['yliMK735_uncorr'], 
    'iNL895_corr': config['models']['yliNL895_corr'],
    'iNL895_uncorr': config['models']['yliNL895_uncorr'],
    'PpaMBEL1254': config['models']['ppaMBEL1254'],
    'iYli21': config['models']['yli21'],
    'iMT1026v3': config['models']['ppa1026v3'],
    'iMT1026Chan2017': config['models']['ppa1026Chan'],
    'iLC915': config['models']['ppaiLC915'],
}

empty_report = {
    'SBML_FATAL': [],
    'SBML_ERROR': [],
    'SBML_SCHEMA_ERROR': [],
    'SBML_WARNING': [],
    'COBRA_FATAL': [],
    'COBRA_ERROR': [],
    'COBRA_WARNING': [],
    'COBRA_CHECK': []
}

erros_in_model = []
# iterater models dictionary
for model_name, model_path in models.items():
    # load and validate model
    print(model_name)
    model, report = cobra.io.validate_sbml_model(model_path)
    # check if model is None
    if isinstance(model, type(None)):
        print('Model is None')
        erros_in_model.append('Model not readable')
        print('----------------------------------')
        continue
    equal = equal_reports(report, empty_report)
    if not equal:
        print('Error(s) in report')
        erros_in_model.append('Error(s) in report')
    else:
        print('No errors in report')
        erros_in_model.append('No errors in report')
    print('----------------------------------')
# none: yli647_uncorr, iMT1026Chan2017
# errors: iYali4_corr, iYali4_uncorr, iMK735_uncorr, iNL895_corr, iNL895_uncorr, PpaMBEL1254, iMT1026v3
# no errors: yli647_corr, iYli_2.0_corr, iMK735_corr, iYli21, iLC915

In [51]:
# # fast validation of config['models']['iYL619_PCP']
# model, report = cobra.io.validate_sbml_model(config['models']['iYL619_PCP'])
# show_differences(report, empty_report)

# fast validation of config['models']['yli647_corr']
model, report = cobra.io.validate_sbml_model(config['models']['yli647_corr'])
show_differences(report, empty_report)
model


<Model COBRAModel at 0x2e8d837f0>

In [34]:
# table of results

# create data frame from models.keys() and erros_in_model
model_errors = pd.DataFrame.from_dict({'Model_Name': list(models.keys()), 'Error': erros_in_model})
# filter model_errors for all models without error
no_errors = model_errors[model_errors['Error'] == 'No errors in report']
no_errors_models = no_errors['Model_Name'].tolist()
# => only yli647_corr, iYli_2.0_corr, iMK735_corr, iYli21, iLC915 have no errors

# ### Not loadable: 
# # yli647_uncorr, iMT1026Chan2017 
# not_loadable = ['yli647_uncorr', 'iMT1026Chan2017'] # from model validation

# ### Loadable: 
# loadable_models = {}
# for model_name, model_path in models.items():
#     if not model_name in not_loadable:
#         loadable_models[model_name] = model_path

# # investigate the error/warning types
# model_problems = {}
# for model_name in loadable_models.keys():
#     if model_name in no_errors_models:
#         continue
#     print(model_name)
#     model, report = cobra.io.validate_sbml_model(models[model_name])
#     model_problems[model_name] = show_differences(report, empty_report)
#     if _verbose:
#         for key, value in report.items():
#             print(f'{key}: {value}')
#         # print('----------------------------------')
#     # print(show_differences(report, empty_report))
#     print('----------------------------------')
# print("Types of model errors/warnings:")
# print(model_problems)


## print errors of loadable models with warnings (very detailed)
for model_name in loadable_models.keys():
    if model_name in no_errors_models:
        continue
    print(model_name)
    model, report = cobra.io.validate_sbml_model(loadable_models[model_name])
    for key, value in report.items():
        print(f'{key}: {value}')
    print('----------------------------------')

# 3.21 min with printing out all errors/warnings

iYali4_corr
SBML_FATAL: []
SBML_ERROR: ["E0 (Error): SBML component consistency (fbc, L16); 'fbc:reaction' must refer to valid reaction; The value of the attribute 'fbc:reaction' of a <fluxObjective> object must be the identifier of an existing <reaction> object defined in the enclosing <model> object.\nReference: L3V1 Fbc V3, Section 3.7\n The <fluxObjective> refers to a reaction with id 'biomass_C' that does not exist within the <model>.\n"]
SBML_SCHEMA_ERROR: []
COBRA_FATAL: []
COBRA_ERROR: []
COBRA_CHECK: []
----------------------------------
iYali4_uncorr
SBML_FATAL: []
SBML_ERROR: []
SBML_SCHEMA_ERROR: []
COBRA_FATAL: []
COBRA_ERROR: []
COBRA_CHECK: []
----------------------------------
iMK735_uncorr
SBML_FATAL: []
SBML_ERROR: []
SBML_SCHEMA_ERROR: []
COBRA_FATAL: []
COBRA_ERROR: []
COBRA_CHECK: []
----------------------------------
iNL895_corr
SBML_FATAL: []
SBML_ERROR: ["E0 (Error): SBML component consistency (core, L15047); Cannot have a reaction with neither reactants nor pro

In [43]:
read_write_models = {
    'iYLI647_corr_corr_read_write': '/Users/ampholyt/Coding/BSEP22/Code/With_Bockmayr/carbon-souces-yli/data/models/read_write_cobrapy/iYLI647_corr_corr_read_write.xml',
    'iYali4_corr_v2_read_write': '/Users/ampholyt/Coding/BSEP22/Code/With_Bockmayr/carbon-souces-yli/data/models/read_write_cobrapy/iYali4_corr_v2_read_write.xml',
    'iYali4_uncorrected_read_write': '/Users/ampholyt/Coding/BSEP22/Code/With_Bockmayr/carbon-souces-yli/data/models/read_write_cobrapy/iYali4_uncorrected_read_write.xml',
    'iYli_2_read_write': '/Users/ampholyt/Coding/BSEP22/Code/With_Bockmayr/carbon-souces-yli/data/models/read_write_cobrapy/iYli_2_read_write.xml',
    'iMK735_corr_read_write': '/Users/ampholyt/Coding/BSEP22/Code/With_Bockmayr/carbon-souces-yli/data/models/read_write_cobrapy/iMK735_corr_read_write.xml',
    'iMK735_v2_read_write': '/Users/ampholyt/Coding/BSEP22/Code/With_Bockmayr/carbon-souces-yli/data/models/read_write_cobrapy/Yli_iMK735_v2_read_write.xml',
    'iNL895_corr_read_write': '/Users/ampholyt/Coding/BSEP22/Code/With_Bockmayr/carbon-souces-yli/data/models/read_write_cobrapy/iNL895_corr_read_write.xml',
    'iNL895_read_write': '/Users/ampholyt/Coding/BSEP22/Code/With_Bockmayr/carbon-souces-yli/data/models/read_write_cobrapy/Yli_iNL895_read_write.xml',
    'PpaMBEL1254_read_write': '/Users/ampholyt/Coding/BSEP22/Code/With_Bockmayr/carbon-souces-yli/data/models/read_write_cobrapy/PpaMBEL1254_read_write.xml',
    'iYli21_v2_read_write': '/Users/ampholyt/Coding/BSEP22/Code/With_Bockmayr/carbon-souces-yli/data/models/read_write_cobrapy/iYli21_v2_read_write.xml',
    'iMT1026v3_v2_read_write': '/Users/ampholyt/Coding/BSEP22/Code/With_Bockmayr/carbon-souces-yli/data/models/read_write_cobrapy/Ppa_iMT1026v3_v2_read_write.xml',
    'iLC915_MODEL1507180065_read_write': '/Users/ampholyt/Coding/BSEP22/Code/With_Bockmayr/carbon-souces-yli/data/models/read_write_cobrapy/Ppa_iLC915_MODEL1507180065_read_write.xml',
}

## print errors of loadable models with warnings (very detailed)
for model_name, model_path in read_write_models.items():
    if model_name in no_errors_models:
        continue
    print(model_name)
    model, report = cobra.io.validate_sbml_model(model_path)
    
    for key, value in report.items():
        print(f'{key}: {value}')
    print(show_differences(report, empty_report))
    print('----------------------------------')

# iYLI647_corr still non error model
# iLC915 still non error model
# Fixed iYali4 (corr and uncor)
# iMK735_v2_read_write: set objective is the only error remaining
# Hat nichts gebracht für iNL895_corr / iNL895_corr_read_write
# iNL895_read_write: no errors anymore
# Additional error: Uniqueness of metaid attribute violated PpaMBEL1254_read_write/ PpaMBEL1254
# iMT1026v3: chemical formula error/ warning remains

# => hat slightly was gebracht, aber nicht für jedes Model


iYLI647_corr_corr_read_write
SBML_FATAL: []
SBML_ERROR: []
SBML_SCHEMA_ERROR: []
COBRA_FATAL: []
COBRA_ERROR: []
COBRA_CHECK: []
[]
----------------------------------
iYali4_corr_v2_read_write
SBML_FATAL: []
SBML_ERROR: []
SBML_SCHEMA_ERROR: []
COBRA_FATAL: []
COBRA_ERROR: []
COBRA_CHECK: []
[]
----------------------------------
iYali4_uncorrected_read_write
SBML_FATAL: []
SBML_ERROR: []
SBML_SCHEMA_ERROR: []
COBRA_FATAL: []
COBRA_ERROR: []
COBRA_CHECK: []
[]
----------------------------------
iYli_2_read_write
SBML_FATAL: []
SBML_ERROR: []
SBML_SCHEMA_ERROR: []
COBRA_FATAL: []
COBRA_ERROR: []
COBRA_CHECK: []
[]
----------------------------------
iMK735_corr_read_write
SBML_FATAL: []
SBML_ERROR: []
SBML_SCHEMA_ERROR: []
COBRA_FATAL: []
COBRA_ERROR: []
COBRA_CHECK: []
[]
----------------------------------
iMK735_v2_read_write
SBML_FATAL: []
SBML_ERROR: ["E0 (Error): SBML component consistency (fbc, L28770); An <objective> must have one <listOfFluxObjectives>.; An <objective> object must

In [24]:
# store error types in table (results/quality)
# error types dict to dataframe second column (errors/warnings) should be a list.
error_type_tbl = pd.DataFrame([model_problems])
# transpose dataframe
error_type_tbl = error_type_tbl.transpose()
print(error_type_tbl.index)
# index to column
error_type_tbl.reset_index(inplace=True)
# rename column
error_type_tbl.columns = ['Model Name', 'Error Type(s)']
error_type_tbl
error_type_tbl.to_csv('../results/quality/error_type_table.csv',index=False, sep=';')

Index(['iYali4_corr', 'iYali4_uncorr', 'iMK735_uncorr', 'iNL895_corr',
       'iNL895_uncorr', 'PpaMBEL1254', 'iMT1026v3'],
      dtype='object')


#### check if models are fixable with reading and writing (All loadable models have fixable errors)

###### Checking specific models (iYali4_corr, iYali4_uncorr)

In [ ]:
# fixing specific models

# # check iYali4_corr error (set objective and write the model)
# outpath = './test_models/iYali4_corr.xml'
# model, report = cobra.io.validate_sbml_model(models['iYali4_corr'])
# model.objective = 'biomass_C'
# cobra.io.write_sbml_model(model, outpath)
# # read it again and check the report 
# model, report = cobra.io.validate_sbml_model(outpath)
# for key, value in report.items():
#     print(f'{key}: {value}')
# print('----------------------------------')

# # check iYali4_uncorr
# outpath = './test_models/iYali4_uncorr.xml'
# model, report = cobra.io.validate_sbml_model(models['iYali4_uncorr'])
# # write the model
# cobra.io.write_sbml_model(model, outpath)
# # read it again and check the report
# model, report = cobra.io.validate_sbml_model(outpath)
# for key, value in report.items():
#     print(f'{key}: {value}')
# print('----------------------------------')

##### Read and write all loadable models with warnings or errors

In [64]:
# read and write all models to new files and check their reports afterwards
def read_and_write_model(model_name, model_path, outpath):
    '''Reads and writes the model to a new file'''
    model = cobra.io.read_sbml_model(model_path)
    cobra.io.write_sbml_model(model, outpath)
    return model

def read_and_return_report(model_path, verbose=False):
    '''Reads and prints the report of the model'''
    model, report = cobra.io.validate_sbml_model(model_path)
    if verbose:
        for key, value in report.items():
            print(f'{key}: {value}')
    return report

for model_name in loadable_models.keys():
    if model_name in no_errors_models:
        continue
    print(model_name)
    model = read_and_write_model(model_name, models[model_name], f'./test_models/{model_name}.xml')
    report = read_and_return_report(model_path)
    equal = equal_reports(report, empty_report)
    if equal:
        print('No errors in report')
    else:
        print('Error(s) in report')
    print('----------------------------------')

iYali4_corr


NameError: name 'read_and_return_report' is not defined

In [18]:
# get fixed models in dict format
fixed_models = {}
for model_name in loadable_models.keys():
    if model_name in no_errors_models:
        continue
    new_model_path = f'./test_models/{model_name}.xml'
    # print(f"'{model_name}_fixed': '{new_model_path}',")
    fixed_models[f'{model_name}_fixed'] = new_model_path
fixed_models

#### dict of fixed models
# {
#     'iYali4_corr_fixed': './test_models/iYali4_corr.xml',
#     'iYali4_uncorr_fixed': './test_models/iYali4_uncorr.xml',
#     'iMK735_uncorr_fixed': './test_models/iMK735_uncorr.xml',
#     'iNL895_corr_fixed': './test_models/iNL895_corr.xml',
#     'iNL895_uncorr_fixed': './test_models/iNL895_uncorr.xml',
#     'PpaMBEL1254_fixed': './test_models/PpaMBEL1254.xml',
#     'iMT1026v3_fixed': './test_models/iMT1026v3.xml',
# }

### 
# {'iYali4_corr_fixed': './test_models/iMT1026v3.xml',
#  'iYali4_uncorr_fixed': './test_models/iMT1026v3.xml',
#  'iMK735_uncorr_fixed': './test_models/iMT1026v3.xml',
#  'iNL895_corr_fixed': './test_models/iMT1026v3.xml',
#  'iNL895_uncorr_fixed': './test_models/iMT1026v3.xml',
#  'PpaMBEL1254_fixed': './test_models/iMT1026v3.xml',
#  'iMT1026v3_fixed': './test_models/iMT1026v3.xml'}


### Biomass reactions used
# {'iYali4_corr_fixed': './test_models/iMT1026v3.xml',
#  'iYali4_uncorr_fixed': './test_models/iMT1026v3.xml',
#  'iMK735_uncorr_fixed': './test_models/iMT1026v3.xml',
#  'iNL895_corr_fixed': './test_models/iMT1026v3.xml',
#  'iNL895_uncorr_fixed': './test_models/iMT1026v3.xml',
#  'PpaMBEL1254_fixed': './test_models/iMT1026v3.xml',
#  'iMT1026v3_fixed': 'Ex_biomass'}
    # {
    #     'biomass': 'Ex_biomass',
    #     'glucose': '',
    #     'glycerol': '',
    #     'methanol': '',
    #     'O2': '',
    #     'CO2': '',
    # }

{'iYali4_corr_fixed': './test_models/iYali4_corr.xml',
 'iYali4_uncorr_fixed': './test_models/iYali4_uncorr.xml',
 'iMK735_uncorr_fixed': './test_models/iMK735_uncorr.xml',
 'iNL895_corr_fixed': './test_models/iNL895_corr.xml',
 'iNL895_uncorr_fixed': './test_models/iNL895_uncorr.xml',
 'PpaMBEL1254_fixed': './test_models/PpaMBEL1254.xml',
 'iMT1026v3_fixed': './test_models/iMT1026v3.xml'}

In [17]:
# all COBRA_WARNINGs: 
# COBRA_WARNING: ['Model does not contain SBML fbc package information.', ...]
## => Fixable with reading and writing?!

# iYali4_corr SBML_ERROR: Reaction with id 'biomass_C' is not found
## => Fixable with setting objective to biomass_C and write model
## valid Model of iYali4_corr without errors in test_models folder

# iYali4_uncorr: SBML_WARNING:
## => Fixable with reading and writing!
## valid Model of iYali4_corr without errors in test_models folder

# # iMK735_uncorr: {} nur CORBA_WARNING
# iNL895_corr: SBML_ERROR
# iNL895_uncorr: COBRA_WARNING
# PpaMBEL1254: COBRA_ERROR
# iMT1026v3 COBRA_CHECK: formulas not in correct format (contain brackets)

['yli647_corr', 'iYli_2.0_corr', 'iMK735_corr', 'iYli21', 'iLC915']

In [21]:
# check report of fixed models
erros_in_model = []
report_list = []
# iterater models dictionary
for model_name, model_path in fixed_models.items():
    # load and validate model
    print(model_name)
    model, report = cobra.io.validate_sbml_model(model_path)
    report_list.append(report)
    equal = equal_reports(report, empty_report)
    if not equal:
        print('Error(s) in report')
        erros_in_model.append('Error(s) in report')
    else:
        print('No errors in report')
        erros_in_model.append('No errors in report')
    print('----------------------------------')
    

iYali4_corr_fixed
No errors in report
----------------------------------
iYali4_uncorr_fixed
No errors in report
----------------------------------
iMK735_uncorr_fixed
Error(s) in report
----------------------------------
iNL895_corr_fixed
Error(s) in report
----------------------------------
iNL895_uncorr_fixed
No errors in report
----------------------------------
PpaMBEL1254_fixed
Error(s) in report
----------------------------------
iMT1026v3_fixed
Error(s) in report
----------------------------------


In [24]:
# list of models fixed through reading and writing: ['iYali4_corr_fixed', 'iYali4_uncorr_fixed', 'iNL895_uncorr_fixed']
[model_name for model_name in fixed_models.keys() if not model_name in not_fixed]

['iYali4_corr_fixed', 'iYali4_uncorr_fixed', 'iNL895_uncorr_fixed']

In [22]:
# interesting models (still with errors)
# load reports of not fixed models
# dict of model_name and index in fixed_models
not_fixed = ['iMK735_uncorr_fixed', 'iNL895_corr_fixed', 'PpaMBEL1254_fixed', 'iMT1026v3_fixed']
counter = 0
for model_name, model_path in fixed_models.items():
    if model_name in not_fixed:
        print(model_name)
        print(report_list[counter])
        print('----------------------------------')
    counter += 1



iMK735_uncorr_fixed
{'SBML_FATAL': [], 'SBML_ERROR': ["E0 (Error): SBML component consistency (fbc, L28770); An <objective> must have one <listOfFluxObjectives>.; An <objective> object must have one and only one instance of the <listOfFluxObjectives> object. \nReference: L3V1 Fbc V3, Section 3.6\n <objective> 'obj' has no listOfFluxObjectives.\n"], 'SBML_SCHEMA_ERROR': [], 'SBML_WARNING': [], 'COBRA_FATAL': [], 'COBRA_ERROR': ['No objective coefficients in model. Unclear what should be optimized'], 'COBRA_WARNING': [], 'COBRA_CHECK': []}
----------------------------------
iNL895_corr_fixed
{'SBML_FATAL': [], 'SBML_ERROR': ["E0 (Error): SBML component consistency (core, L15047); Cannot have a reaction with neither reactants nor products; A <reaction> definition must contain at least one <speciesReference>, either in its <listOfReactants> or its <listOfProducts>. A reaction without any reactant or product species is not permitted, regardless of whether the reaction has any modifier speci

### Load all models and try fba of initial conditions
- should result in a table of models and if there were errors while fba of initial conditions

In [9]:
## pfba
# from cobra.flux_analysis.parsimonious import pfba 
# # flux balance analysis
# pfba_solution = pfba(model)
# pfba_solution

## optimize the model
# model.optimize()

<Solution 64132.848 at 0x2e08f8970>

In [16]:
# fba of all loadable models => table if error occures
summary_list_fba = []
fba_errors_fba = []
for model_name, model_path in loadable_models.items():
    print(model_name)
    model = cobra.io.read_sbml_model(model_path)
    try:
        sol = model.optimize()
        sum = model.summary()
        print(sum)
        summary_list_fba.append(sum)
        fba_errors_fba.append(round(sol.objective_value, 4))
    except:
        print('Error in FBA')
        fba_errors_fba.append('Error of initial condition')
    print('-------------------')
# all fixed models with 0.058 as objective value

# which model has a working fba?
# data frame from model_name and fba_errors
# fba_errors_df = pd.DataFrame.from_dict({'Model_Name': list(fixed_models.keys()), 'FBA_Error': fba_errors})

# which objective function is used?
# model.objective.reaction.id


yli647_corr
Objective
1.0 biomass_C = 1.1398166174413986

Uptake
------
Metabolite  Reaction    Flux  C-Number  C-Flux
  glc_D[e] EX_glc(e)      10         6 100.00%
      h[e]   EX_h(e)  0.3853         0   0.00%
    nh4[e] EX_nh4(e)   7.772         0   0.00%
     o2[e]  EX_o2(e)   14.99         0   0.00%
     pi[e]  EX_pi(e)  0.3853         0   0.00%
    so4[e] EX_so4(e) 0.07735         0   0.00%

Secretion
---------
Metabolite  Reaction   Flux  C-Number  C-Flux
biomass[c]   EX_biom  -1.14         0   0.00%
    co2[e] EX_co2(e) -16.79         1 100.00%
    h2o[e] EX_h2o(e) -32.53         0   0.00%

-------------------
iYali4_corr
Objective
1.0 biomass_C = 1.3775770431148784

Uptake
------
Metabolite Reaction    Flux  C-Number  C-Flux
     m1031     1654   9.309         0   0.00%
      m511     1714      10         6 100.00%
     m1339     1992   13.52         0   0.00%
      m215     2005  0.3632         0   0.00%
     m1113     2060 0.09349         0   0.00%

Secretion
---------
Meta

/Users/ampholyt/Coding/BSEP22/Code/With_Bockmayr/EFM_calculation_cobamp/venv/lib/python3.8/site-packages/cobra/util/solver.py:554: UserWarning: Solver status is 'infeasible'.
  warn(f"Solver status is '{status}'.", UserWarning)


Error in FBA
-------------------
iNL895_corr
Objective
1.0 biomass_C = 1.753511791088482

Uptake
------
Metabolite       Reaction   Flux  C-Number C-Flux
    s_1162 r_128_exchange 0.8535         0  0.00%
    s_1209 r_134_exchange 0.4624         0  0.00%
    s_1348 r_150_exchange  0.119         0  0.00%
    s_0431  r_38_exchange  11.85         0  0.00%
    s_0547  r_51_exchange     10         0  0.00%

Secretion
---------
Metabolite      Reaction    Flux  C-Number C-Flux
    s_0463        r_1814  -1.754         0  0.00%
    s_0472 r_41_exchange -0.7851         0  0.00%

-------------------
iNL895_uncorr
Objective
1.0 r_1814 + 1.0 r_021_xxx = 3.887928552536729

Uptake
------
Metabolite    Reaction    Flux  C-Number C-Flux
  s_0764_b EX_s_0764_b   112.5         0  0.00%
  s_2845_b EX_s_2845_b    11.1         0  0.00%
  s_2858_b EX_s_2858_b      10         0  0.00%
  s_2935_b EX_s_2935_b       2         0  0.00%
  s_2941_b EX_s_2941_b  0.4034         0  0.00%
  s_2957_b EX_s_2957_b   3.676

In [17]:
# which model has a working fba?
# data frame from model_name and fba_errors
fba_errors_fba_df = pd.DataFrame.from_dict({'Model Name': list(loadable_models.keys()), 'FBA Results': fba_errors_fba})

fba_errors_fba_df
fba_errors_fba_df.to_csv('./test_models/initial_fba_results_yli_ppa.csv', index=False)

In [26]:
loadable_models

{'yli647_corr': '../data/models/Yarrowia_lipolytica/iYLI647/iYLI647_corr_corr.xml',
 'iYali4_corr': '../data/models/Yarrowia_lipolytica/iYali4/iYali4_corr_v2.xml',
 'iYali4_uncorr': '../data/models/Yarrowia_lipolytica/iYali4/iYali4_uncorrected.xml',
 'iYli_2.0_corr': '../data/models/Yarrowia_lipolytica/iYli_2.0/iYli_2.0_corr_corr_v2.xml',
 'iMK735_corr': '../data/models/Yarrowia_lipolytica/iMK735/iMK735_corr.xml',
 'iMK735_uncorr': '../data/models/Yarrowia_lipolytica/iMK735/Yli_iMK735_v2.xml',
 'iNL895_corr': '../data/models/Yarrowia_lipolytica/iNL895/iNL895_corr.xml',
 'iNL895_uncorr': '../data/models/Yarrowia_lipolytica/iNL895/Yli_iNL895.xml',
 'PpaMBEL1254': '../data/models/Pichia_pastoris/PpaMBEL1254/PpaMBEL1254.xml',
 'iYli21': '../data/models/Yarrowia_lipolytica/iYli21/iYli21_v2.xml',
 'iMT1026v3': '../data/models/Pichia_pastoris/iMT1026/Ppa_iMT1026v3_v2.xml',
 'iLC915': '../data/models/Pichia_pastoris/iLC915/Ppa_iLC915_MODEL1507180065.xml'}

In [28]:
model = cobra.io.read_sbml_model(loadable_models['iYali4_corr'])
model

<Model iYali4_corr at 0x2cea12880>

In [30]:
model.summary()